In [ ]:
import ipysheet
from analytics import CreditIndex

In [ ]:
sheet = ipysheet.sheet(rows=3, columns=4, column_headers=False, row_headers=False)
ipysheet.cell(0, 0, 'indices', read_only=True)
ipysheet.cell(0, 1, 'notionals', read_only=True)
ipysheet.cell(0, 2, 'price', read_only=True)
ipysheet.cell(0, 3, 'newref', read_only=True)
cells = {}
cells[(1, 0)] = ipysheet.cell(1, 0, '', background_color='yellow')
cells[(2, 0)] = ipysheet.cell(2, 0, '', background_color='yellow')
cells[(1, 1)] = ipysheet.cell(1, 1, -10_000_000, read_only=True)
cells[(2, 1)] = ipysheet.cell(2, 1, 10_000_000, background_color='yellow')
cells[(1, 2)] = ipysheet.cell(1, 2, background_color='yellow')
cells[(2, 2)] = ipysheet.cell(2, 2, background_color='yellow')
cells[(1, 3)] = ipysheet.cell(1, 3, background_color='yellow')
cells[(2, 3)] = ipysheet.cell(2, 3, read_only=True)

indices = {}
def create_indices(change):
    global indices
    index_str = change['new']
    index_type = index_str[:2]
    series = int(index_str[2:])
    indices[index_str] = CreditIndex(index_type, series, '5yr')

def change_notional(change):
    global indices
    index2 = indices[cells[(2, 0)].value]
    index1 = indices[cells[(1, 0)].value]
    index2.notional = change['new']
    index1.notional = -index2.notional * index2.factor * index2.risky_annuity / index1.risky_annuity / index1.factor
    cells[(1, 1)].value = index1.notional
    
def set_price(change):
    global indices, debug
    index_str = cells[(change['owner'].row_start, change['owner'].column_start -2)].value
    indices[index_str].price = change['new']

debug = None
def set_new_ref(change):
    global indices, debug
    index1 = indices[cells[(1, 0)].value]
    index2 = indices[cells[(2, 0)].value]
    old_price1, old_price2 = index1.price, index2.price
    old_pv1 = index1.pv
    index1.price = change['new']
    pv_change = index1.pv - old_pv1
    index2.pv -= pv_change
    cells[(2, 3)].value = index2.price
    index1.price = old_price1
    index2.price = old_price2
    
cells[(1, 0)].observe(create_indices, 'value')
cells[(2, 0)].observe(create_indices, 'value')
cells[(2, 1)].observe(change_notional, 'value')
cells[(1, 2)].observe(set_price, 'value')
cells[(2, 2)].observe(set_price, 'value')
cells[(1, 3)].observe(set_new_ref, 'value')


In [ ]:
sheet